<a href="https://colab.research.google.com/github/vishnu-chand/highlightsGenerator/blob/master/highlightsGenerator.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install -q youtube_dl

     |████████████████████████████████| 1.8MB 2.8MB/s 


In [2]:
import os
import cv2
import youtube_dl
import numpy as np
from glob import glob
from moviepy import editor as mpy
from matplotlib import pyplot as plt
from ipywidgets import interact_manual

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)1933312/45929032 bytes (4.2%)5693440/45929032 bytes (12.4%)9560064/45929032 bytes (20.8%)13385728/45929032 bytes (29.1%)17334272/45929032 bytes (37.7%)21004288/45929032 bytes (45.7%)24911872/45929032 bytes (54.2%)28835840/45929032 bytes (62.8%)32784384/45929032 bytes (71.4%)36642816/45929032 bytes (79.8%)40607744/45929032 bytes (88.4%)44630016/45929032 bytes (97.2%)

In [3]:
def getVideo(url, maxSizeMB=80):
    downloader = f"youtube-dl -f 'best[filesize<{maxSizeMB}M]' '{url}'"
    error = os.system(f"mkdir videos;cd videos;{downloader} --print-json --restrict-filenames -o '%(id)s.%(ext)s'")
    if error:  
        print(f'failed to fetch "{url}", error: {error}')

urls = [
        'https://www.youtube.com/watch?v=EgWqoWG5V80', 
        'https://www.youtube.com/watch?v=QD2hxpQd_b0&t=35s', 
        'https://www.youtube.com/watch?v=ynG6tkLO3SQ', 
        # 'https://www.youtube.com/watch?v=EiIHHiJdVo8',
        'https://www.youtube.com/watch?v=jPfeLG2fPeU',
        'https://www.youtube.com/watch?v=i0RrKolSMgw&t=91s',
        ]
for url in urls:
    getVideo(url)
vpaths = glob(f'videos/*')
for vpath in vpaths:
    print(vpath)

videos/QD2hxpQd_b0.mp4
videos/jPfeLG2fPeU.mp4
videos/EgWqoWG5V80.mp4
videos/ynG6tkLO3SQ.mp4
videos/i0RrKolSMgw.mp4


In [0]:
# this will show the strength of volume
def getVolumeBar(clip, x, delta, beta=.8):
    fps, w, h = int(clip.fps), clip.size[0], 50
    bar = np.zeros((h, w, 3), 'u1')
    x = (x - x.min()) / x.max()
    score = x[0]
    imgs = []
    for vol in x:
        for _ in range(fps * delta):
            score = score * beta + vol * (1 - beta)
            color = (255, 0, 0)
            if score > .25:
                color = (255, 255, 0)
            if score > .5:
                color = (0, 255, 0)
            img = cv2.line(bar.copy(), (0, 0), (int(score * w), 0), color, h, cv2.LINE_AA)
            imgs.append(img)
    eneryBar = mpy.ImageSequenceClip(imgs, clip.fps)
    return eneryBar

In [0]:
def getKeyFrames(ipeaks, peaks):
    # consider sequence which are 10% louder than the average
    # and return the frame index where sound is maxima
    # for each sequence return one maxima
    highlights = peaks > 1.1 * peaks.mean()
    keyFrames, maxima, imaxima = [], 0, 0
    for ipeak, peak, highlight in zip(ipeaks, peaks, highlights):
        if highlight:
            if peak > maxima:
                maxima, imaxima = peak, ipeak
        elif maxima:
            keyFrames.append(imaxima)
            maxima = 0  # reset maxima
    if maxima:
        keyFrames.append(imaxima)
    return keyFrames

In [0]:
highlights = None
def getHighlights(vpath=vpaths, clipStart=0, clipStop=-25, delta=3):
    clip = mpy.VideoFileClip(vpath).subclip(clipStart, clipStop)
    x = [clip.audio.subclip(i, i + delta).to_soundarray() for i in range(0, int(clip.duration), delta)]
    energy = np.array([np.sqrt((i ** 2).sum()) for i in x])
    energyBar = getVolumeBar(clip, energy, delta)
    kernel = [-1, 2, -1]
    edges = cv2.filter2D(energy.reshape(1, -1), -1, np.array([kernel])).astype(int).ravel() > 0
    ienergy = np.arange(energy.size)
    ipeaks, peaks = ienergy[edges], energy[edges]
    keyFrames = getKeyFrames(ipeaks, peaks)
    plt.figure(figsize=(20,10))
    plt.plot(energy, label="singnal")
    plt.plot(ipeaks, peaks, 'o', label="peaks")
    plt.plot(keyFrames, energy[keyFrames], 'o', label="highlights")
    plt.legend(loc="upper left")
    clips = []
    for ix, keyFrame in enumerate(keyFrames, 1):
        start, stop = delta * (keyFrame - 2), delta * (keyFrame + 2)
        start, stop = max(0, start), min(stop, clip.duration)
        img = np.zeros((50, clip.size[0], 3), 'u1')
        img = cv2.putText(img, f"HIGHLIGHT: {ix}", (30, 30), 1, 2, (128, 197, 30), thickness=2)
        nText = int((stop - start) * clip.fps)
        textClip = mpy.ImageSequenceClip([img] * nText, fps=clip.fps)
        video = mpy.clips_array([
            [clip.subclip(start, stop)],
            [textClip],
            [energyBar.subclip(start, stop)]
        ])
        clips.append(video)
    global highlights
    highlights = mpy.concatenate(clips)
    plt.show()

In [7]:
m = interact_manual(getHighlights, vpath=vpaths)

interactive(children=(Dropdown(description='vpath', options=('videos/QD2hxpQd_b0.mp4', 'videos/jPfeLG2fPeU.mp4…

In [8]:
stop = min(55, highlights.duration)
highlights.subclip(0,stop).ipython_display(loop=1, autoplay=1)

100%|██████████| 1439/1439 [00:07<00:00, 201.10it/s]
